In [53]:
import os
import requests
import random
import pickle
KEY = '91mTqXFEeSaCIbjC0fuaB1RABk4HANqS4I91qRBN'
KEY2 = 'flLQZGa0kx8opciUA6M7R9iLPwfFPj5yFKKlCiVb'

MOST_RECENT_HR_BILL = 6536 #1490
MOST_RECENT_S_BILL = 3548  #606
CONGRESS = 114

In [130]:
def getJSON(webpage):
    headers = {
        'X-API-Key': KEY
    }
    r = requests.get(webpage, headers=headers)
    return r.json()

def getSponsors(bill_id, congress, progress = 'introduced'):
    '''Returns (PrimarySponsor, [cosponsors]) for specified bill_id and congress strings. Returns () if faulty'''
    '''progress = 'introduced', 'became law'                                                                '''
    edge = getJSON('https://api.propublica.org/congress/v1/' + str(congress) + '/bills/' + bill_id + '/cosponsors.json')
    toReturn = False
    if edge['status'] == 'OK':
        print(edge['results'][0]['latest_major_action'][:17])
        if progress =='introduced':
            toReturn = True
        elif progress == 'became law':
            toReturn = edge['results'][0]['latest_major_action'][:17] == 'Became Public Law'           
                
    if toReturn:
        return (edge['results'][0]['sponsor_id'], [cosponsor['cosponsor_id'] for cosponsor in edge['results'][0]['cosponsors']])
    else:
        return ()
    
def getMembers(congress):
    '''takes congress session and Returns dictioanry of congress member ids with value 0'''
    senate_members = getJSON('https://api.propublica.org/congress/v1/'+ str(congress) +'/senate/members.json')
    house_members = getJSON('https://api.propublica.org/congress/v1/'+ str(congress) +'/house/members.json')
    senateList, houseList = [],[]
    if senate_members['status'] == 'OK':
        senateList = [(senator['id'],0) for senator in senate_members['results'][0]['members']]
    if house_members['status'] == 'OK':
        houseList = [(rep['id'],0) for rep in house_members['results'][0]['members']]
    return dict(senateList + houseList)

def getNameIDPairing(congress):
    senate_members = getJSON('https://api.propublica.org/congress/v1/'+ str(congress) +'/senate/members.json')
    house_members = getJSON('https://api.propublica.org/congress/v1/'+ str(congress) +'/house/members.json')
    senateList, houseList = [],[]
    if senate_members['status'] == 'OK':
        senateList = [(senator['id'], senator['first_name'] + ' ' + senator['last_name'] + '(' + senator['party'] + ')') for senator in senate_members['results'][0]['members']]
    if house_members['status'] == 'OK':
        houseList = [(rep['id'],rep['first_name'] + ' ' + rep['last_name'] + '(' + rep['party'] + ')') for rep in house_members['results'][0]['members']]
    return dict(senateList + houseList)
    
    
def buildGraph(members, congress):
    graph = {}
    for m in members:
        graph[m] = []
    
    for i in range(1, MOST_RECENT_HR_BILL+1):
        print("At HR{0}".format(i))
        edge = getSponsors("hr{0}".format(i), congress)
        if edge: # not (,)
            graph[edge[0]].extend(edge[1])
    
    for i in range(1, MOST_RECENT_S_BILL+1):
        print("At S{0}".format(i))
        edge = getSponsors("s{0}".format(i), congress)
        if edge: # not (,)
            graph[edge[0]].extend(edge[1])
        
    return graph

def buildFilteredGraph(members, congress):
    graph = {}
    for m in members:
        graph[m] = []
    
    for i in range(1, MOST_RECENT_HR_BILL+1):
        print("At HR{0}".format(i))
        edge = getSponsors("hr{0}".format(i), congress, 'became law')
        if edge: # not (,)
            graph[edge[0]].extend(edge[1])
    
    for i in range(1, MOST_RECENT_S_BILL+1):
        print("At S{0}".format(i))
        edge = getSponsors("s{0}".format(i), congress, 'became law')
        if edge: # not (,)
            graph[edge[0]].extend(edge[1])
        
    return graph

def ranker(members, graph, p=.15, iterations=1000000):
    assert len(graph) == len(members)
    member_list = list(graph.keys())
    current = random.choice(member_list)
    members[current] += 1
    for i in range(iterations):
#         if i % 10 == 0:
#             print("Iteration: {0}".format(i))
        if len(graph[current]) == 0 or random.random() < p:
            current = random.choice(member_list)
#             print("reset")

        else:
            neighbors = graph[current]
            current = neighbors[random.randint(0, len(neighbors)-1)]
            print("Continue")
        members[current] += 1
    return members


def save_obj(obj, name ):
    with open(name + '.pkl', 'wb') as f:
        pickle.dump(obj, f, pickle.HIGHEST_PROTOCOL)

def load_obj(name ):
    with open(name + '.pkl', 'rb') as f:
        return pickle.load(f)


In [56]:
# members = getMembers(CONGRESS)
# graph = buildGraph(members, CONGRESS)
# names = getNameIDPairing(CONGRESS)
filteredGraph = buildFilteredGraph

save_obj(graph, 'congress' + str(CONGRESS) + '_filteredGraph')
# save_obj(members, 'congress' + str(CONGRESS) + '_members')
# save_obj(graph, 'congress' + str(CONGRESS) + '_graph')
# save_obj(names, 'congress' + str(CONGRESS) + '_names')

At HR1
At HR2
At HR3
At HR4
At HR5
At HR6
At HR7
At HR8
At HR9
At HR10
At HR11
At HR12
At HR13
At HR14
At HR15
At HR16
At HR17
At HR18
At HR19
At HR20
At HR21
At HR22
At HR23
At HR24
At HR25
At HR26
At HR27
At HR28
At HR29
At HR30
At HR31
At HR32
At HR33
At HR34
At HR35
At HR36
At HR37
At HR38
At HR39
At HR40
At HR41
At HR42
At HR43
At HR44
At HR45
At HR46
At HR47
At HR48
At HR49
At HR50
At HR51
At HR52
At HR53
At HR54
At HR55
At HR56
At HR57
At HR58
At HR59
At HR60
At HR61
At HR62
At HR63
At HR64
At HR65
At HR66
At HR67
At HR68
At HR69
At HR70
At HR71
At HR72
At HR73
At HR74
At HR75
At HR76
At HR77
At HR78
At HR79
At HR80
At HR81
At HR82
At HR83
At HR84
At HR85
At HR86
At HR87
At HR88
At HR89
At HR90
At HR91
At HR92
At HR93
At HR94
At HR95
At HR96
At HR97
At HR98
At HR99
At HR100
At HR101
At HR102
At HR103
At HR104
At HR105
At HR106
At HR107
At HR108
At HR109
At HR110
At HR111
At HR112
At HR113
At HR114
At HR115
At HR116
At HR117
At HR118
At HR119
At HR120
At HR121
At HR122
At HR123
A

In [95]:
graph = load_obj('congress' + str(CONGRESS) + '_graph')
members = load_obj('congress' + str(CONGRESS) + '_members')
names = load_obj('congress' + str(CONGRESS) + '_names')

In [ ]:
ranking = ranker(members, graph,.5)
member_ranks = [pair[0] for pair in sorted(members.items(), key = lambda item: item[1], reverse=True)]
top_score = members[member_ranks[0]]
for i in range(len(member_ranks)):
    print("%d %f: %s" % (i+1,members[member_ranks[i]]/top_score, names[member_ranks[i]]))

Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
Continue
C

In [68]:
test = getJSON('https://api.propublica.org/congress/v1/members/N000147/bills/introduced.json')

In [76]:
test2 = getJSON('https://api.propublica.org/congress/v1/114/bills/hr6477/cosponsors.json')

In [112]:
test3 = getJSON('https://api.propublica.org/congress/v1/114/bills/hr6431/cosponsors.json')

In [116]:
test3['results'][0]['latest_major_action'][:17] == 'Became Public Law'

True

In [131]:
test4 = getSponsors('6477', 114,'became law')

KeyError: 'results'

In [129]:
test4

()